#MedNext M 5 for BraTS 2021 (Task 1)

*Source: Isensee, F., Jaeger, P.F., Kohl, S.A.A. et al. "nnU-Net: a self-configuring method for deep learning-based biomedical image segmentation." Nat Methods (2020). https://doi.org/10.1038/s41592-020-01008-z*

*https://github.com/MIC-DKFZ/nnUNet*

####1. Downloading dataset

In [ ]:
from google.colab import files
files.upload()


Saving kaggle.json to kaggle.json


{'kaggle.json': b'{\n  "username": "anastasiasaprina",\n  "key": "KGAT_93b03a40a8fec761f7cec4a29e6e31ef"\n}'}

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install -q kaggle

!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json


In [ ]:
!mkdir -p /content/data
%cd /content/data

/content/data


In [ ]:
!kaggle datasets download -d dschettler8845/brats-2021-task1

Dataset URL: https://www.kaggle.com/datasets/dschettler8845/brats-2021-task1
License(s): copyright-authors
100% 12.3G/12.3G [00:28<00:00, 609MB/s]
100% 12.3G/12.3G [00:28<00:00, 462MB/s]


In [ ]:
!unzip -q brats-2021-task1.zip

In [ ]:
!tar -xf /content/data/BraTS2021_Training_Data.tar -C /content/data


####2. Model installation

In [ ]:
!pip install -q git+https://github.com/MIC-DKFZ/MedNeXt.git


  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 156.3/156.3 kB 13.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.0/77.0 kB 8.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.7/43.7 kB 4.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 52.6/52.6 MB 43.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 83.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.3/13.3 MB 112.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 96.4/96.4 kB 9.3 MB/s eta 0:00:00


####3. Preprocessing

In [ ]:
import os

# nnU-Net v1 / MedNeXt environment variables
os.environ["nnUNet_raw_data_base"] = "/content/nnUNet_raw_data_base"
os.environ["nnUNet_preprocessed"] = "/content/nnUNet_preprocessed"
os.environ["RESULTS_FOLDER"] = "/content/nnUNet_results"

# create folders
os.makedirs(os.path.join(os.environ["nnUNet_raw_data_base"], "nnUNet_raw_data"), exist_ok=True)
os.makedirs(os.environ["nnUNet_preprocessed"], exist_ok=True)
os.makedirs(os.environ["RESULTS_FOLDER"], exist_ok=True)


In [ ]:
files.upload() # add split_brats2021_whole_tumor.json

Saving split_brats2021_whole_tumor.json to split_brats2021_whole_tumor (2).json


{'split_brats2021_whole_tumor (2).json': b'{\n  "train": [\n    "BraTS2021_01209",\n    "BraTS2021_01055",\n    "BraTS2021_00538",\n    "BraTS2021_01545",\n    "BraTS2021_01481",\n    "BraTS2021_01272",\n    "BraTS2021_00684",\n    "BraTS2021_00811",\n    "BraTS2021_01541",\n    "BraTS2021_00140",\n    "BraTS2021_01328",\n    "BraTS2021_00787",\n    "BraTS2021_00477",\n    "BraTS2021_01182",\n    "BraTS2021_01132",\n    "BraTS2021_00172",\n    "BraTS2021_00071",\n    "BraTS2021_01373",\n    "BraTS2021_01654",\n    "BraTS2021_01640",\n    "BraTS2021_01399",\n    "BraTS2021_01463",\n    "BraTS2021_01279",\n    "BraTS2021_01345",\n    "BraTS2021_01581",\n    "BraTS2021_00314",\n    "BraTS2021_00547",\n    "BraTS2021_01240",\n    "BraTS2021_01572",\n    "BraTS2021_00043",\n    "BraTS2021_01383",\n    "BraTS2021_01067",\n    "BraTS2021_01269",\n    "BraTS2021_00123",\n    "BraTS2021_00379",\n    "BraTS2021_01412",\n    "BraTS2021_01360",\n    "BraTS2021_01247",\n    "BraTS2021_00575",\n    

In [ ]:
SPLIT_JSON = "/content/split_brats2021_whole_tumor.json"


In [ ]:
import os, json
from glob import glob

TASK_DIR = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021"
labelsTr = os.path.join(TASK_DIR, "labelsTr")


with open(SPLIT_JSON, "r") as f:
    split = json.load(f)

train_ids = set(split["train"])
val_ids   = set(split["val"])
test_ids  = set(split["test"])

# какие кейсы реально есть в dataset (по labelsTr)
existing = set([os.path.basename(p).replace(".nii.gz","") for p in glob(os.path.join(labelsTr, "*.nii.gz"))])

print("Existing cases in nnU-Net Task:", len(existing))
print("Train/Val/Test sizes:", len(train_ids), len(val_ids), len(test_ids))

print("Missing in existing (train):", len(train_ids - existing))
print("Missing in existing (val):",   len(val_ids - existing))
print("Missing in existing (test):",  len(test_ids - existing))

# важная проверка на пересечения
print("Intersections: train∩val:", len(train_ids & val_ids),
      "train∩test:", len(train_ids & test_ids),
      "val∩test:", len(val_ids & test_ids))


Existing cases in nnU-Net Task: 1251
Train/Val/Test sizes: 876 250 125
Missing in existing (train): 0
Missing in existing (val): 0
Missing in existing (test): 0
Intersections: train∩val: 0 train∩test: 0 val∩test: 0


In [ ]:
import os, json, pickle

PREP_DIR = "/content/nnUNet_preprocessed/Task501_BraTS2021"
SPLIT_JSON = "/content/split_brats2021_whole_tumor.json"

with open(SPLIT_JSON, "r") as f:
    split = json.load(f)

train_ids = sorted(split["train"])
val_ids   = sorted(split["val"])
test_ids  = sorted(split["test"])

# nnU-Net v1 expects list of dicts with 'train' and 'val'
fold0 = {"train": train_ids, "val": val_ids}

# Делаем 5 folds, все одинаковые, чтобы код nnU-Net не ломался
splits = [fold0, fold0, fold0, fold0, fold0]

os.makedirs(PREP_DIR, exist_ok=True)
out_path = os.path.join(PREP_DIR, "splits_final.pkl")

with open(out_path, "wb") as f:
    pickle.dump(splits, f)

print("Wrote:", out_path)
print("Fold0 train:", len(train_ids), "val:", len(val_ids), "test held out:", len(test_ids))


Wrote: /content/nnUNet_preprocessed/Task501_BraTS2021/splits_final.pkl
Fold0 train: 876 val: 250 test held out: 125


In [ ]:
import os, json, shutil
import numpy as np
import nibabel as nib
from glob import glob

# nnU-Net v1 / MedNeXt env vars
os.environ["nnUNet_raw_data_base"] = "/content/nnUNet_raw_data_base"
os.environ["nnUNet_preprocessed"] = "/content/nnUNet_preprocessed"
os.environ["RESULTS_FOLDER"] = "/content/nnUNet_results"

SRC = "/content/data"               # твои папки BraTS2021_00000, ...
TASK = "Task501_BraTS2021"
DST = os.path.join(os.environ["nnUNet_raw_data_base"], "nnUNet_raw_data", TASK)

imagesTr = os.path.join(DST, "imagesTr")
labelsTr = os.path.join(DST, "labelsTr")
os.makedirs(imagesTr, exist_ok=True)
os.makedirs(labelsTr, exist_ok=True)

label_files = sorted(glob(os.path.join(labelsTr, "*.nii.gz")))
case_ids = [os.path.splitext(os.path.splitext(os.path.basename(f))[0])[0] for f in label_files]

training_list = [{"image": f"./imagesTr/{cid}.nii.gz", "label": f"./labelsTr/{cid}.nii.gz"} for cid in case_ids]


patient_dirs = sorted([p for p in glob(os.path.join(SRC, "BraTS2021_*")) if os.path.isdir(p)])
print("Patients found:", len(patient_dirs))
print("Example:", os.path.basename(patient_dirs[0]) if patient_dirs else "NONE")

def remap_seg(seg):
    seg = seg.astype(np.uint8)
    out = np.zeros_like(seg, dtype=np.uint8)
    out[seg == 1] = 1
    out[seg == 2] = 2
    out[seg == 4] = 3
    return out

copied, skipped = 0, 0

for pdir in patient_dirs:
    pid = os.path.basename(pdir)  # BraTS2021_00000
    case_id = pid

    paths = {
        0: os.path.join(pdir, f"{pid}_t1.nii.gz"),
        1: os.path.join(pdir, f"{pid}_t1ce.nii.gz"),
        2: os.path.join(pdir, f"{pid}_t2.nii.gz"),
        3: os.path.join(pdir, f"{pid}_flair.nii.gz"),
    }
    seg_path = os.path.join(pdir, f"{pid}_seg.nii.gz")

    if any(not os.path.exists(p) for p in paths.values()) or not os.path.exists(seg_path):
        skipped += 1
        continue

    for ch in range(4):
        shutil.copy(paths[ch], os.path.join(imagesTr, f"{case_id}_{ch:04d}.nii.gz"))

    seg_nii = nib.load(seg_path)
    seg = seg_nii.get_fdata()
    seg_r = remap_seg(seg)
    nib.save(
        nib.Nifti1Image(seg_r, seg_nii.affine, seg_nii.header),
        os.path.join(labelsTr, f"{case_id}.nii.gz")
    )

    copied += 1

print("Copied:", copied, "| Skipped:", skipped)

dataset_json = {
    "name": "BraTS2021",
    "description": "BraTS2021 Task1 for MedNeXt (nnU-Net v1 format)",
    "tensorImageSize": "3D",
    "reference": "BraTS 2021",
    "licence": "see source",
    "release": "1.0",
    "modality": {"0": "T1", "1": "T1ce", "2": "T2", "3": "FLAIR"},
    "labels": {"0": "background", "1": "necrotic_core", "2": "edema", "3": "enhancing_tumor"},
    "numTraining": len(case_ids),
    "numTest": 0,
    "training": training_list,
    "test": [],
    "file_ending": ".nii.gz"
}

with open(os.path.join(DST, "dataset.json"), "w") as f:
    json.dump(dataset_json, f, indent=2)

print("Task created at:", DST)
print("dataset.json:", os.path.join(DST, "dataset.json"))
print("imagesTr example:", sorted(os.listdir(imagesTr))[:3])
print("labelsTr example:", sorted(os.listdir(labelsTr))[:3])


Patients found: 1251
Example: BraTS2021_00000
Copied: 1251 | Skipped: 0
Task created at: /content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021
dataset.json: /content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/dataset.json
imagesTr example: ['BraTS2021_00000_0000.nii.gz', 'BraTS2021_00000_0001.nii.gz', 'BraTS2021_00000_0002.nii.gz']
labelsTr example: ['BraTS2021_00000.nii.gz', 'BraTS2021_00002.nii.gz', 'BraTS2021_00003.nii.gz']


In [ ]:
import json
p="/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/dataset.json"
d=json.load(open(p))
print("has training:", "training" in d)
print("len(training):", len(d["training"]))
print("first entry:", d["training"][0])


has training: True
len(training): 1251
first entry: {'image': './imagesTr/BraTS2021_00000.nii.gz', 'label': './labelsTr/BraTS2021_00000.nii.gz'}


In [ ]:
!pip install -q nnunet==1.7.1


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 276.6/276.6 kB 19.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done


In [ ]:
!python -c "import nnunet; print('nnunet OK')"




Please cite the following paper when using nnUNet:

Isensee, F., Jaeger, P.F., Kohl, S.A.A. et al. "nnU-Net: a self-configuring method for deep learning-based biomedical image segmentation." Nat Methods (2020). https://doi.org/10.1038/s41592-020-01008-z


If you have questions or suggestions, feel free to open an issue at https://github.com/MIC-DKFZ/nnUNet

nnunet OK


In [ ]:
!mednextv1_plan_and_preprocess -t 501 -pl3d ExperimentPlanner3D_v21_customTargetSpacing_1x1x1 -pl2d None


Streaming output truncated to the last 5000 lines.

no resampling necessary
no resampling necessary
before: {'spacing': array([1., 1., 1.]), 'spacing_transposed': array([1., 1., 1.]), 'data.shape (data is transposed)': (4, 138, 172, 129)} 
after:  {'spacing': array([1., 1., 1.]), 'data.shape (data is resampled)': (4, 138, 172, 129)} 

1 2593
2 10000
3 10000
saving:  /content/nnUNet_preprocessed/Task501_BraTS2021/nnUNetData_plans_v2.1_trgSp_1x1x1_stage0/BraTS2021_01146.npz
no resampling necessary
no resampling necessary
before: {'spacing': array([1., 1., 1.]), 'spacing_transposed': array([1., 1., 1.]), 'data.shape (data is transposed)': (4, 137, 166, 147)} 
after:  {'spacing': array([1., 1., 1.]), 'data.shape (data is resampled)': (4, 137, 166, 147)} 

1 1719
2 10000
3 6929
saving:  /content/nnUNet_preprocessed/Task501_BraTS2021/nnUNetData_plans_v2.1_trgSp_1x1x1_stage0/BraTS2021_01297.npz
1 10000
2 9892
3 10000
saving:  /content/nnUNet_preprocessed/Task501_BraTS2021/nnUNetData_plans_v2.

In [ ]:
!ls /content/nnUNet_preprocessed



Task501_BraTS2021


In [ ]:
!ls /content/nnUNet_preprocessed/Task501_BraTS2021

dataset.json		nnUNetData_plans_v2.1_trgSp_1x1x1_stage0
dataset_properties.pkl	nnUNetPlansv2.1_trgSp_1x1x1_plans_3D.pkl
gt_segmentations


In [ ]:
!ls -lah /content/nnUNet_preprocessed/Task501_BraTS2021 | grep -i split
!find /content/nnUNet_preprocessed/Task501_BraTS2021 -maxdepth 2 -type f -iname "*split*" -print


In [ ]:
!mednextv1_train --help | head -n 40


usage: mednextv1_train [-h] [-val] [-c] [-p P] [--use_compressed_data]
                       [--deterministic] [--npz] [--find_lr] [--valbest]
                       [--fp32] [--val_folder VAL_FOLDER] [--disable_saving]
                       [--disable_postprocessing_on_folds]
                       [--val_disable_overwrite] [--disable_next_stage_pred]
                       [--sample_by_frequency]
                       [-pretrained_weights PRETRAINED_WEIGHTS]
                       [-resample_weights]
                       network network_trainer task fold

positional arguments:
  network
  network_trainer
  task                  can be task name or task id
  fold                  0, 1, ..., 5 or 'all'

options:
  -h, --help            show this help message and exit
  -val, --validation_only
                        use this if you want to only run the validation
  -c, --continue_training
                        use this if you want to continue a training
  -p P                  p

In [ ]:
os.environ["nnUNet_results"] = "/content/drive/MyDrive/brats"

####4. Training

In [ ]:
!mednextv1_train 3d_fullres nnUNetTrainerV2_MedNeXt_M_kernel3 501 0 -p nnUNetPlansv2.1_trgSp_1x1x1


###############################################
I am running the following nnUNet: 3d_fullres
My trainer class is:  <class 'nnunet_mednext.training.network_training.MedNeXt.nnUNetTrainerV2_MedNeXt.nnUNetTrainerV2_MedNeXt_M_kernel3'>
For that I will be using the following configuration:
num_classes:  3
modalities:  {0: 'T1', 1: 'T1ce', 2: 'T2', 3: 'FLAIR'}
use_mask_for_norm OrderedDict({0: True, 1: True, 2: True, 3: True})
keep_only_largest_region None
min_region_size_per_class None
min_size_per_class None
normalization_schemes OrderedDict({0: 'nonCT', 1: 'nonCT', 2: 'nonCT', 3: 'nonCT'})
stages...

stage:  0
{'batch_size': 2, 'num_pool_per_axis': [5, 5, 5], 'patch_size': [128, 128, 128], 'median_patient_size_in_voxels': array([140, 171, 137]), 'current_spacing': array([1., 1., 1.]), 'original_spacing': array([1., 1., 1.]), 'do_dummy_2D_data_aug': np.False_, 'pool_op_kernel_sizes': [[2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2], [2, 2, 2]], 'conv_kernel_sizes': [[3, 3, 3], [3, 3, 3], [3, 3

In [ ]:
IMAGES_TR = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/imagesTr"
PRED_OUT  = "/content/mednext_pred_test"

SPLIT_JSON = "/content/split_brats2021_whole_tumor.json"

TASK_ID = 501
FOLD = 0
CONFIG = "3d_fullres"
PLANS = "nnUNetPlansv2.1_trgSp_1x1x1"


In [ ]:
import os, json, shutil, glob

TMP_TEST = "/content/mednext_imagesTs_test"
os.makedirs(TMP_TEST, exist_ok=True)
os.makedirs(PRED_OUT, exist_ok=True)

with open(SPLIT_JSON) as f:
    split = json.load(f)

test_ids = split["test"]
print("Test cases:", len(test_ids))

# очищаем папку
for f in os.listdir(TMP_TEST):
    os.remove(os.path.join(TMP_TEST, f))

for pid in test_ids:
    files = glob.glob(os.path.join(IMAGES_TR, f"{pid}_*.nii.gz"))
    if len(files) == 0:
        raise RuntimeError(f"No files found for {pid} in imagesTr")

    for fpath in files:
        shutil.copy(fpath, TMP_TEST)

print("Prepared test images:", len(os.listdir(TMP_TEST)))


Test cases: 125
Prepared test images: 500


In [ ]:
import os
os.environ["RESULTS_FOLDER"] = "/content/nnUNet_results"
print("RESULTS_FOLDER =", os.environ["RESULTS_FOLDER"])


RESULTS_FOLDER = /content/nnUNet_results


####5. Evaluation

In [ ]:
import os, json, shutil, glob

IMAGES_TR = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/imagesTr"
SPLIT_JSON = "/content/split_brats2021_whole_tumor.json"

TMP_TEST = "/content/mednext_imagesTs_test"
os.makedirs(TMP_TEST, exist_ok=True)

with open(SPLIT_JSON, "r") as f:
    split = json.load(f)

test_ids = split["test"]
print("Test cases:", len(test_ids))

# очистка папки
for fn in os.listdir(TMP_TEST):
    os.remove(os.path.join(TMP_TEST, fn))

# копируем 4 модальности каждого тестового кейса
for pid in test_ids:
    files = glob.glob(os.path.join(IMAGES_TR, f"{pid}_*.nii.gz"))
    if len(files) == 0:
        raise RuntimeError(f"No images found for {pid} in {IMAGES_TR}")
    for fpath in files:
        shutil.copy(fpath, TMP_TEST)

print("Files in TMP_TEST:", len(os.listdir(TMP_TEST)))
print("Example:", sorted(os.listdir(TMP_TEST))[:8])


Test cases: 125
Files in TMP_TEST: 500
Example: ['BraTS2021_00016_0000.nii.gz', 'BraTS2021_00016_0001.nii.gz', 'BraTS2021_00016_0002.nii.gz', 'BraTS2021_00016_0003.nii.gz', 'BraTS2021_00028_0000.nii.gz', 'BraTS2021_00028_0001.nii.gz', 'BraTS2021_00028_0002.nii.gz', 'BraTS2021_00028_0003.nii.gz']


In [ ]:
PRED_OUT = "/content/mednext_pred_test"
os.makedirs(PRED_OUT, exist_ok=True)


In [ ]:
!ls /content/nnUNet_results/nnUNet/3d_fullres/Task501_BraTS2021


nnUNetTrainerV2_MedNeXt_M_kernel3__nnUNetPlansv2.1_trgSp_1x1x1


In [ ]:
import os
os.environ["TORCH_FORCE_NO_WEIGHTS_ONLY_LOAD"] = "1"


In [ ]:
!mednextv1_predict \
  -i /content/mednext_imagesTs_test \
  -o /content/mednext_pred_test \
  -t 501 \
  -m 3d_fullres \
  -f 0 \
  -p nnUNetPlansv2.1_trgSp_1x1x1 \
  -tr nnUNetTrainerV2_MedNeXt_M_kernel3 \
  -chk model_best \
  --save_npz


using model stored in  /content/nnUNet_results/nnUNet/3d_fullres/Task501_BraTS2021/nnUNetTrainerV2_MedNeXt_M_kernel3__nnUNetPlansv2.1_trgSp_1x1x1
This model expects 4 input modalities for each image
Found 125 unique case ids, here are some examples: ['BraTS2021_00063' 'BraTS2021_00158' 'BraTS2021_01216' 'BraTS2021_01659'
 'BraTS2021_00528' 'BraTS2021_01258' 'BraTS2021_01198' 'BraTS2021_00203'
 'BraTS2021_01392' 'BraTS2021_01009']
If they don't look right, make sure to double check your filenames. They must end with _0000.nii.gz etc
number of cases: 125
number of cases that still need to be predicted: 125
emptying cuda cache
loading parameters for folds, [0]
using the following model files:  ['/content/nnUNet_results/nnUNet/3d_fullres/Task501_BraTS2021/nnUNetTrainerV2_MedNeXt_M_kernel3__nnUNetPlansv2.1_trgSp_1x1x1/fold_0/model_best.model']
/usr/local/lib/python3.12/dist-packages/nnunet_mednext/training/model_restore.py:147: UserWarning: Environment variable TORCH_FORCE_NO_WEIGHTS_ONLY_L

In [ ]:
# ===== Install deps (если вдруг нет) =====
!pip -q install nibabel scipy pandas

import os, json
import numpy as np
import nibabel as nib
import pandas as pd
from scipy.ndimage import binary_erosion, distance_transform_edt

# ===== Paths =====
SPLIT_JSON = "/content/split_brats2021_whole_tumor.json"
GT_DIR = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/labelsTr"
PRED_DIR = "/content/mednext_pred_test"
OUT_CSV = "/content/mednext_test_metrics.csv"

# ===== Helpers =====
def load_nii(path):
    return nib.load(path).get_fdata()

def regions_from_mask(mask):
    """
    GT: 1,2,4
    Pred: 1,2,3 (MedNeXt remap)
    """
    mask = mask.astype(np.int16)
    uniq = set(np.unique(mask))

    # detect ET label
    if 4 in uniq:
        et = 4
    elif 3 in uniq:
        et = 3
    else:
        et = 4  # empty ET

    WT = mask > 0
    TC = (mask == 1) | (mask == et)
    ET = (mask == et)
    return WT, TC, ET

def dice(a, b, eps=1e-8):
    a = a.astype(bool)
    b = b.astype(bool)
    if a.sum() + b.sum() == 0:
        return 1.0
    return (2 * np.logical_and(a, b).sum() + eps) / (a.sum() + b.sum() + eps)

def surface(mask):
    er = binary_erosion(mask)
    return mask & (~er)

def hd95(a, b, spacing):
    if a.sum() == 0 and b.sum() == 0:
        return 0.0
    if a.sum() == 0 or b.sum() == 0:
        return np.nan

    sa = surface(a)
    sb = surface(b)

    dt_a = distance_transform_edt(~sa, sampling=spacing)
    dt_b = distance_transform_edt(~sb, sampling=spacing)

    dists = np.concatenate([dt_b[sa], dt_a[sb]])
    return float(np.percentile(dists, 95))

# ===== Load split =====
with open(SPLIT_JSON) as f:
    split = json.load(f)

test_ids = split["test"]
print("Test cases:", len(test_ids))

# ===== Main loop =====
rows = []

for pid in test_ids:
    gt_path = os.path.join(GT_DIR, f"{pid}.nii.gz")
    pr_path = os.path.join(PRED_DIR, f"{pid}.nii.gz")

    if not os.path.exists(pr_path):
        print("Missing prediction for", pid)
        continue

    gt_img = nib.load(gt_path)
    pr_img = nib.load(pr_path)

    gt = gt_img.get_fdata()
    pr = pr_img.get_fdata()

    spacing = gt_img.header.get_zooms()[:3]

    gt_WT, gt_TC, gt_ET = regions_from_mask(gt)
    pr_WT, pr_TC, pr_ET = regions_from_mask(pr)

    rows.append({
        "pid": pid,
        "dice_WT": dice(pr_WT, gt_WT),
        "dice_TC": dice(pr_TC, gt_TC),
        "dice_ET": dice(pr_ET, gt_ET),
        "hd95_WT": hd95(pr_WT, gt_WT, spacing),
        "hd95_TC": hd95(pr_TC, gt_TC, spacing),
        "hd95_ET": hd95(pr_ET, gt_ET, spacing),
    })

df = pd.DataFrame(rows)

# ===== Summary =====
summary = df[[
    "dice_WT","dice_TC","dice_ET",
    "hd95_WT","hd95_TC","hd95_ET"
]].agg(["mean","median"])

print("\n=== SUMMARY ===")
print(summary)

df.to_csv(OUT_CSV, index=False)
print("\nSaved per-case metrics to:", OUT_CSV)

df.head()


Test cases: 125

=== SUMMARY ===
         dice_WT   dice_TC   dice_ET   hd95_WT   hd95_TC   hd95_ET
mean    0.935303  0.907332  0.858353  3.971676  4.404705  4.273131
median  0.949030  0.952941  0.912950  2.000000  1.414214  1.414214

Saved per-case metrics to: /content/mednext_test_metrics.csv


pid   dice_WT   dice_TC   dice_ET    hd95_WT    hd95_TC  \
0  BraTS2021_01347  0.959624  0.564544  0.530466   1.414214   9.361818   
1  BraTS2021_01045  0.930505  0.968499  0.937463   3.464102   1.414214   
2  BraTS2021_01156  0.935985  0.981611  0.908761   2.449490   1.000000   
3  BraTS2021_00596  0.973012  0.982348  0.940103   1.000000   1.000000   
4  BraTS2021_01479  0.837307  0.531705  0.700006  13.892444  17.000000   

    hd95_ET  
0  9.170591  
1  1.414214  
2  1.000000  
3  1.000000  
4  7.874008

In [ ]:
dice_mean = (dice(pr_WT, gt_WT) + dice(pr_TC, gt_TC) + dice(pr_ET, gt_ET)).mean()
dice_mean = round(dice_mean, 4)
dice_mean

0.9003

####6. 3D volume visualisation

In [ ]:
!pip -q install plotly scikit-image nibabel


In [ ]:
import os, json
import numpy as np
import nibabel as nib
from skimage.measure import marching_cubes
import plotly.graph_objects as go

SPLIT_JSON = "/content/split_brats2021_whole_tumor.json"
GT_DIR     = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/labelsTr"
PRED_DIR   = "/content/mednext_pred_test"

def load_nii(path):
    img = nib.load(path)
    data = img.get_fdata()
    spacing = img.header.get_zooms()[:3]  # (sx,sy,sz) or (x,y,z) depending on orientation, but ok for relative scale
    return data, spacing

def detect_et_label(mask):
    uniq = set(np.unique(mask.astype(np.int16)).tolist())
    if 4 in uniq:
        return 4
    if 3 in uniq:
        return 3
    return 4

def brats_regions(mask):
    mask = mask.astype(np.int16)
    et = detect_et_label(mask)
    WT = mask > 0
    TC = (mask == 1) | (mask == et)
    ET = (mask == et)
    return WT, TC, ET

def make_mesh(binary_vol, spacing=(1.0,1.0,1.0), step_size=2):
    """
    binary_vol: (X,Y,Z) or (D,H,W) array. Works as long as consistent.
    step_size: higher = faster, lower = more detailed.
    """
    vol = binary_vol.astype(np.uint8)
    if vol.sum() == 0:
        return None

    verts, faces, _, _ = marching_cubes(vol, level=0.5, step_size=step_size)
    # scale vertices by voxel spacing
    verts = verts * np.array(spacing)[None, :]
    return verts, faces

def add_mesh(fig, mesh, name, opacity=0.35, showlegend=True, line_width=0, dash=None):
    if mesh is None:
        return
    verts, faces = mesh
    x, y, z = verts.T
    i, j, k = faces.T
    fig.add_trace(go.Mesh3d(
        x=x, y=y, z=z,
        i=i, j=j, k=k,
        opacity=opacity,
        name=name,
        showlegend=showlegend,
        flatshading=True
    ))

# choose patient
with open(SPLIT_JSON, "r") as f:
    split = json.load(f)

pid = split["test"][0]  # можешь заменить на конкретный id
print("Patient:", pid)

gt_path   = os.path.join(GT_DIR, f"{pid}.nii.gz")
pred_path = os.path.join(PRED_DIR, f"{pid}.nii.gz")

gt, spacing = load_nii(gt_path)
pred, _     = load_nii(pred_path)

gt_WT, gt_TC, gt_ET = brats_regions(gt)
pr_WT, pr_TC, pr_ET = brats_regions(pred)

# build meshes (step_size=2 обычно норм, 1 будет красивее но медленнее)
meshes = {
    "GT WT": make_mesh(gt_WT, spacing=spacing, step_size=2),
    "Pred WT": make_mesh(pr_WT, spacing=spacing, step_size=2),
    "GT TC": make_mesh(gt_TC, spacing=spacing, step_size=2),
    "Pred TC": make_mesh(pr_TC, spacing=spacing, step_size=2),
    "GT ET": make_mesh(gt_ET, spacing=spacing, step_size=2),
    "Pred ET": make_mesh(pr_ET, spacing=spacing, step_size=2),
}

# interactive figure
fig = go.Figure()

# Добавим WT как базу, TC и ET сверху
add_mesh(fig, meshes["GT WT"],   "GT WT",   opacity=0.20)
add_mesh(fig, meshes["Pred WT"], "Pred WT", opacity=0.20)

add_mesh(fig, meshes["GT TC"],   "GT TC",   opacity=0.35)
add_mesh(fig, meshes["Pred TC"], "Pred TC", opacity=0.35)

add_mesh(fig, meshes["GT ET"],   "GT ET",   opacity=0.55)
add_mesh(fig, meshes["Pred ET"], "Pred ET", opacity=0.55)

fig.update_layout(
    title=f"{pid}: 3D meshes (WT/TC/ET), GT vs Pred",
    scene=dict(
        xaxis_title="X (mm)",
        yaxis_title="Y (mm)",
        zaxis_title="Z (mm)",
        aspectmode="data"
    ),
    legend=dict(itemsizing="constant"),
    height=800
)

fig.show()


Patient: BraTS2021_01347


In [ ]:
import os, json
import numpy as np
import nibabel as nib
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from skimage.measure import marching_cubes

SPLIT_JSON = "/content/split_brats2021_whole_tumor.json"
GT_DIR     = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/labelsTr"
PRED_DIR   = "/content/mednext_pred_test"

def load_nii(path):
    img = nib.load(path)
    data = img.get_fdata()
    spacing = img.header.get_zooms()[:3]
    return data, spacing

def detect_et_label(mask):
    uniq = set(np.unique(mask.astype(np.int16)).tolist())
    if 4 in uniq:
        return 4
    if 3 in uniq:
        return 3
    return 4  # fallback

def make_mesh(binary_vol, spacing=(1.0,1.0,1.0), step_size=3):
    vol = binary_vol.astype(np.uint8)
    if vol.sum() == 0:
        return None
    verts, faces, _, _ = marching_cubes(vol, level=0.5, step_size=step_size)
    verts = verts * np.array(spacing)[None, :]
    return verts, faces

def mesh3d_from_binary(binary_vol, spacing, color, name, opacity=0.55, step_size=3):
    m = make_mesh(binary_vol, spacing=spacing, step_size=step_size)
    if m is None:
        return None
    verts, faces = m
    return go.Mesh3d(
        x=verts[:,0], y=verts[:,1], z=verts[:,2],
        i=faces[:,0], j=faces[:,1], k=faces[:,2],
        color=color,
        opacity=opacity,
        name=name,
        flatshading=True,
        showscale=False
    )

# pick patient
with open(SPLIT_JSON, "r") as f:
    split = json.load(f)

pid = split["test"][0]  # можно заменить на конкретный
print("Patient:", pid)

gt, spacing = load_nii(os.path.join(GT_DIR, f"{pid}.nii.gz"))
pr, _       = load_nii(os.path.join(PRED_DIR, f"{pid}.nii.gz"))

gt = gt.astype(np.uint8)
pr = pr.astype(np.uint8)

gt_et = detect_et_label(gt)
pr_et = detect_et_label(pr)

# masks per class
gt_1  = (gt == 1)
gt_2  = (gt == 2)
gt_etm = (gt == gt_et)     # ET (3 или 4)

pr_1  = (pr == 1)
pr_2  = (pr == 2)
pr_etm = (pr == pr_et)     # ET (3 или 4)

# colors: как в твоём примере
COL1 = "red"     # label 1
COL2 = "yellow"  # label 2
COLET = "orange" # ET

# traces
gt_traces = [
    mesh3d_from_binary(gt_1, spacing, COL1,  "GT label 1", opacity=0.60, step_size=2),
    mesh3d_from_binary(gt_2, spacing, COL2,  "GT label 2", opacity=0.45, step_size=2),
    mesh3d_from_binary(gt_etm, spacing, COLET, f"GT ET ({gt_et})", opacity=0.55, step_size=2),
]

pr_traces = [
    mesh3d_from_binary(pr_1, spacing, COL1,  "Pred label 1", opacity=0.45, step_size=2),
    mesh3d_from_binary(pr_2, spacing, COL2,  "Pred label 2", opacity=0.35, step_size=2),
    mesh3d_from_binary(pr_etm, spacing, COLET, f"Pred ET ({pr_et})", opacity=0.45, step_size=2),
]

# figure: 2 scenes side-by-side
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{"type": "scene"}, {"type": "scene"}]],
    subplot_titles=("Ground Truth", "Prediction")
)

for t in gt_traces:
    if t is not None:
        fig.add_trace(t, row=1, col=1)

for t in pr_traces:
    if t is not None:
        fig.add_trace(t, row=1, col=2)

camera = dict(eye=dict(x=1.6, y=1.6, z=1.3))

scene_common = dict(
    aspectmode="data",
    camera=camera,
    xaxis=dict(title="X", showbackground=True, backgroundcolor="white", gridcolor="lightgray"),
    yaxis=dict(title="Y", showbackground=True, backgroundcolor="white", gridcolor="lightgray"),
    zaxis=dict(title="Z", showbackground=True, backgroundcolor="white", gridcolor="lightgray"),
)

fig.update_layout(
    title=f"{pid} | 3D tumor classes: GT vs Pred",
    height=780,
    margin=dict(l=0, r=0, t=70, b=0),
    scene=scene_common,
    scene2=scene_common,
    legend=dict(itemsizing="constant")
)

# В Colab обычно стабильнее iframe
fig.show()


Patient: BraTS2021_01347


In [ ]:
out_html = f"/content/{pid}_GT_vs_Pred_3D.html"
fig.write_html(out_html, include_plotlyjs="cdn")
print(out_html)


/content/BraTS2021_01347_GT_vs_Pred_3D.html


In [ ]:
!pip -q install plotly scikit-image kaleido nibabel


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.0/69.0 kB 6.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.3/49.3 kB 4.6 MB/s eta 0:00:00


In [ ]:
!pip install -U kaleido


In [ ]:
import kaleido

In [ ]:
!pip install -U plotly>=6.1.1

In [ ]:
import os, json
import numpy as np
import nibabel as nib
import plotly.graph_objects as go
from skimage.measure import marching_cubes

# ====== SETTINGS ======
SPLIT_JSON = "/content/split_brats2021_whole_tumor.json"

IMAGES_DIR = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/imagesTr"
GT_DIR     = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/labelsTr"
PR_DIR     = "/content/mednext_pred_test"

# choose case
with open(SPLIT_JSON) as f:
    split = json.load(f)
CASE_ID = split["test"][0]   # или вручную "BraTS2021_00714"

# choose modality for brain surface
T1CE_CH = 1  # _0001 = T1ce

# what to visualize: "WT" or "TC" or "ET" or "ALL"
SHOW = "ALL"

OUT_GT = f"/content/{CASE_ID}_GT.png"
OUT_PR = f"/content/{CASE_ID}_PRED.png"

# ====== HELPERS ======
def load_nii(path):
    img = nib.load(path)
    data = img.get_fdata()
    spacing = img.header.get_zooms()[:3]
    return data, spacing

def detect_et_label(mask):
    uniq = set(np.unique(mask.astype(np.int16)).tolist())
    if 4 in uniq:
        return 4
    if 3 in uniq:
        return 3
    return 4

def regions(mask):
    mask = mask.astype(np.int16)
    et = detect_et_label(mask)
    WT = mask > 0
    TC = (mask == 1) | (mask == et)
    ET = (mask == et)
    return WT, TC, ET

def mc_mesh(binary_vol, spacing=(1,1,1), step_size=2):
    if binary_vol.sum() == 0:
        return None
    verts, faces, _, _ = marching_cubes(binary_vol.astype(np.uint8), level=0.5, step_size=step_size)
    verts = verts * np.array(spacing)[None, :]
    return verts, faces

def mesh_trace(vf, name, color, opacity):
    if vf is None:
        return None
    v, f = vf
    x, y, z = v.T
    i, j, k = f.T
    return go.Mesh3d(
        x=x, y=y, z=z, i=i, j=j, k=k,
        name=name, color=color, opacity=opacity,
        flatshading=True, showscale=False,
        lighting=dict(ambient=0.45, diffuse=0.75, specular=0.2, roughness=0.85, fresnel=0.05),
        lightposition=dict(x=200, y=200, z=200),
    )

def make_brain_mesh(t1ce, spacing):
    nz = t1ce[t1ce > 0]
    thr = np.percentile(nz, 10)  # можно 15-30
    brain = (t1ce > thr)
    return mesh_trace(mc_mesh(brain, spacing, step_size=3), "Brain", "lightgray", 0.18)

def build_fig(brain_trace, tumor_traces, title):
    camera = dict(eye=dict(x=1.6, y=1.6, z=1.3))
    fig = go.Figure()
    if brain_trace is not None:
        fig.add_trace(brain_trace)
    for t in tumor_traces:
        if t is not None:
            fig.add_trace(t)

    fig.update_layout(
        title=title,
        height=700,
        margin=dict(l=0, r=0, t=60, b=0),
        scene=dict(
            aspectmode="data",
            camera=camera,
            xaxis=dict(title="x", showbackground=True, backgroundcolor="white", gridcolor="lightgray"),
            yaxis=dict(title="y", showbackground=True, backgroundcolor="white", gridcolor="lightgray"),
            zaxis=dict(title="z", showbackground=True, backgroundcolor="white", gridcolor="lightgray"),
        ),
        legend=dict(itemsizing="constant")
    )
    return fig

# ====== LOAD DATA ======
gt, spacing = load_nii(os.path.join(GT_DIR, f"{CASE_ID}.nii.gz"))
pr, _       = load_nii(os.path.join(PR_DIR, f"{CASE_ID}.nii.gz"))

t1ce, _ = load_nii(os.path.join(IMAGES_DIR, f"{CASE_ID}_{T1CE_CH:04d}.nii.gz"))

gt = gt.astype(np.uint8)
pr = pr.astype(np.uint8)

brain = make_brain_mesh(t1ce, spacing)

gt_WT, gt_TC, gt_ET = regions(gt)
pr_WT, pr_TC, pr_ET = regions(pr)

# colors like your example
COL_WT = "yellow"
COL_TC = "orange"
COL_ET = "red"

def tumor_traces_from_regions(WT, TC, ET, spacing, prefix):
    traces = []
    if SHOW in ("WT", "ALL"):
        traces.append(mesh_trace(mc_mesh(WT, spacing, step_size=2), f"{prefix} WT", COL_WT, 0.45))
    if SHOW in ("TC", "ALL"):
        traces.append(mesh_trace(mc_mesh(TC, spacing, step_size=2), f"{prefix} TC", COL_TC, 0.55))
    if SHOW in ("ET", "ALL"):
        traces.append(mesh_trace(mc_mesh(ET, spacing, step_size=2), f"{prefix} ET", COL_ET, 0.70))
    return traces

gt_traces = tumor_traces_from_regions(gt_WT, gt_TC, gt_ET, spacing, "GT")
pr_traces = tumor_traces_from_regions(pr_WT, pr_TC, pr_ET, spacing, "Pred")

fig_gt = build_fig(brain, gt_traces, f"{CASE_ID} | Ground Truth")
fig_pr = build_fig(brain, pr_traces, f"{CASE_ID} | Prediction")

# show interactive (крутится)
fig_gt.show()
fig_pr.show()

# save png (для слайда)
#fig_gt.write_image(OUT_GT, scale=2)
#fig_pr.write_image(OUT_PR, scale=2)

#print("Saved:", OUT_GT)
#print("Saved:", OUT_PR)


In [ ]:
GT_HTML = f"/content/{CASE_ID}_GT_3D.html"
PR_HTML = f"/content/{CASE_ID}_PRED_3D.html"

fig_gt.write_html(GT_HTML, include_plotlyjs="cdn")
fig_pr.write_html(PR_HTML, include_plotlyjs="cdn")

print("Saved:", GT_HTML)
print("Saved:", PR_HTML)


Saved: /content/BraTS2021_01347_GT_3D.html
Saved: /content/BraTS2021_01347_PRED_3D.html


In [ ]:
import os, json
import numpy as np
import nibabel as nib
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from skimage.measure import marching_cubes

# ======================
# SETTINGS
# ======================
SPLIT_JSON = "/content/split_brats2021_whole_tumor.json"
IMAGES_DIR = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/imagesTr"
GT_DIR     = "/content/nnUNet_raw_data_base/nnUNet_raw_data/Task501_BraTS2021/labelsTr"
PR_DIR     = "/content/mednext_pred_test"

with open(SPLIT_JSON) as f:
    split = json.load(f)

CASE_ID = split["test"][0]   # гарантированно валидный кейс
T1CE_CH = 1                  # _0001

# ======================
# HELPERS
# ======================
def load_nii(path):
    img = nib.load(path)
    return img.get_fdata(), img.header.get_zooms()[:3]

def mc(vol, spacing, step=3):
    if vol.sum() == 0:
        return None
    v, f, _, _ = marching_cubes(vol.astype(np.uint8), level=0.5, step_size=step)
    v = v * np.array(spacing)[None, :]
    return v, f

def mesh(vf, color, opacity, name):
    if vf is None:
        return None
    v, f = vf
    return go.Mesh3d(
        x=v[:,0], y=v[:,1], z=v[:,2],
        i=f[:,0], j=f[:,1], k=f[:,2],
        color=color, opacity=opacity, name=name,
        flatshading=True, showscale=False
    )

# ======================
# LOAD DATA
# ======================
gt, spacing = load_nii(os.path.join(GT_DIR, f"{CASE_ID}.nii.gz"))
pr, _       = load_nii(os.path.join(PR_DIR, f"{CASE_ID}.nii.gz"))
t1ce, _     = load_nii(os.path.join(IMAGES_DIR, f"{CASE_ID}_{T1CE_CH:04d}.nii.gz"))

gt = gt.astype(np.uint8)
pr = pr.astype(np.uint8)

# brain mask
nz = t1ce[t1ce > 0]
brain = t1ce > np.percentile(nz, 20)

# regions (BraTS)
ET = 3 if 3 in np.unique(gt) else 4
gt_WT = gt > 0
gt_TC = (gt == 1) | (gt == ET)
gt_ET = gt == ET

pr_WT = pr > 0
pr_TC = (pr == 1) | (pr == ET)
pr_ET = pr == ET

# ======================
# BUILD FIGURE
# ======================
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{"type": "scene"}, {"type": "scene"}]],
    subplot_titles=("Ground Truth", "Prediction")
)

# brain
brain_mesh = mesh(mc(brain, spacing, step=5), "lightgray", 0.18, "Brain")
fig.add_trace(brain_mesh, row=1, col=1)
fig.add_trace(brain_mesh, row=1, col=2)

# GT
fig.add_trace(mesh(mc(gt_WT, spacing), "yellow", 0.35, "WT"), row=1, col=1)
fig.add_trace(mesh(mc(gt_TC, spacing), "orange", 0.50, "TC"), row=1, col=1)
fig.add_trace(mesh(mc(gt_ET, spacing), "red",    0.70, "ET"), row=1, col=1)

# Pred
fig.add_trace(mesh(mc(pr_WT, spacing), "yellow", 0.35, "WT"), row=1, col=2)
fig.add_trace(mesh(mc(pr_TC, spacing), "orange", 0.50, "TC"), row=1, col=2)
fig.add_trace(mesh(mc(pr_ET, spacing), "red",    0.70, "ET"), row=1, col=2)

camera = dict(eye=dict(x=1.6, y=1.6, z=1.3))

fig.update_layout(
    height=720,
    margin=dict(l=0, r=0, t=60, b=0),
    scene=dict(aspectmode="data", camera=camera),
    scene2=dict(aspectmode="data", camera=camera),
    legend=dict(itemsizing="constant")
)

fig.show()


In [ ]:
out_html = f"/content/{CASE_ID}_GT_vs_PRED_3D.html"
fig.write_html(out_html, include_plotlyjs="cdn")
print("Saved:", out_html)


Saved: /content/BraTS2021_01347_GT_vs_PRED_3D.html
